In [1]:
import json
import os
import time
import random
from PIL import Image
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import shutil

import torch
import torch.nn as nn
import torch.backends.cudnn as cudnn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision import transforms
from torchvision import models
from torchsummary import summary
from sklearn.model_selection import train_test_split

from model_pytorch import EfficientNet
from utils import Bar,Logger, AverageMeter, accuracy, mkdir_p, savefig
from warmup_scheduler import GradualWarmupScheduler

from PIL import ImageFile
ImageFile.LOAD_TRUNCATED_IMAGES = True
import collections

In [2]:
# GPU Device
gpu_id = 3
os.environ['CUDA_VISIBLE_DEVICES'] = str(gpu_id)
use_cuda = torch.cuda.is_available()
print("GPU device %d:" %(gpu_id), use_cuda)

GPU device 3: True


# Arguments

In [3]:
source_dir = '/media/data2/dataset/GAN_ImageData/PGGAN_128/'
target_dir = '/media/data2/dataset/GAN_ImageData/StyleGAN_256/'

In [4]:
pretrained = './log/pggan/128/b1/checkpoint.pth.tar'
resume = ''

In [5]:
# Model
model_name = 'efficientnet-b1' # b0-b7 scale

# Optimization
num_classes = 2
epochs = 5000
start_epoch = 0
train_batch = 12
test_batch = 200
lr = 0.03
schedule = [200, 1500, 3000, 4500, 6000]
momentum = 0
gamma = 0.1 # LR is multiplied by gamma on schedule

# CheckPoint
checkpoint = './log/pggan/128/b1/to_style1/cutmix4' # dir
if not os.path.isdir(checkpoint):
    os.makedirs(checkpoint)
num_workers = 4

# Seed
manual_seed = 7
random.seed(manual_seed)
torch.cuda.manual_seed_all(manual_seed)

# Image
size = (128, 128)

# sp
sp_alpha = 0.1
sp_beta = 0.1
fc_name = 'fc.'

# iterative training
feedback = 0
iter_time = [500, 1000, 1500, 2000, 2500, 3500, 4000, 4500]

# cutmix
cm_prob = 0.5
cm_prob_init = 0.99
cm_prob_low = 0.01

best_acc = 0

In [6]:
state = {}
state['num_classes'] = num_classes
state['epochs'] = epochs
state['start_epoch'] = start_epoch
state['train_batch'] = train_batch
state['test_batch'] = test_batch
state['lr'] = lr
state['schedule'] = schedule
state['momentum'] = momentum
state['gamma'] = gamma

# Dataset

In [7]:
train_dir = os.path.join(target_dir, '100_shot')
source_train_dir = os.path.join(target_dir, '100_shot_pggan_only')
val_target_dir = os.path.join(target_dir, 'validation')
val_source_dir = os.path.join(source_dir, 'validation')

train_aug = transforms.Compose([
    transforms.RandomAffine(degrees=2, translate=(0.02, 0.02), scale=(0.98, 1.02), shear=2, fillcolor=(124,117,104)),
    transforms.Resize(size),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
#     transforms.RandomErasing(p=0.3, scale=(0.02, 0.10), ratio=(0.3, 3.3), value=0, inplace=True),
])
val_aug = transforms.Compose([
    transforms.Resize(size),
    transforms.ToTensor(),
])

# pin_memory : cuda pin memeory use
train_loader = DataLoader(datasets.ImageFolder(train_dir, transform=train_aug),
                          batch_size=train_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
source_train_loader = DataLoader(datasets.ImageFolder(source_train_dir, transform=val_aug),
                                batch_size=train_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_target_loader = DataLoader(datasets.ImageFolder(val_target_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)
val_source_loader = DataLoader(datasets.ImageFolder(val_source_dir, val_aug),
                       batch_size=test_batch, shuffle=True, num_workers=num_workers, pin_memory=True)

# Model

In [8]:
teacher_model = EfficientNet.from_name(model_name, num_classes=num_classes)
student_model = EfficientNet.from_name(model_name, num_classes=num_classes,
                                      override_params={'dropout_rate':0.3, 'drop_connect_rate':0.1})

# Pre-trained
if pretrained:
    print("=> using pre-trained model '{}'".format(pretrained))
    teacher_model.load_state_dict(torch.load(pretrained)['state_dict'])
    student_model.load_state_dict(torch.load(pretrained)['state_dict'])

=> using pre-trained model './log/pggan/128/b1/checkpoint.pth.tar'


In [9]:
teacher_model.to('cuda')
student_model.to('cuda')
cudnn.benchmark = True
print('    Total params: %.2fM' % (sum(p.numel() for p in student_model.parameters())/1000000.0))

    Total params: 6.52M


In [10]:
for param in teacher_model.parameters():
    param.requires_grad = False
teacher_model.eval()

EfficientNet(
  (_conv_stem): Conv2dStaticSamePadding(
    3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False
    (static_padding): ZeroPad2d(padding=(0, 1, 0, 1), value=0.0)
  )
  (_bn0): GroupNorm(8, 32, eps=1e-05, affine=True)
  (_blocks): ModuleList(
    (0): MBConvBlock(
      (_depthwise_conv): Conv2dStaticSamePadding(
        32, 32, kernel_size=(3, 3), stride=[1, 1], groups=32, bias=False
        (static_padding): ZeroPad2d(padding=(1, 1, 1, 1), value=0.0)
      )
      (_bn1): GroupNorm(8, 32, eps=1e-05, affine=True)
      (_se_reduce): Conv2dStaticSamePadding(
        32, 8, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_se_expand): Conv2dStaticSamePadding(
        8, 32, kernel_size=(1, 1), stride=(1, 1)
        (static_padding): Identity()
      )
      (_project_conv): Conv2dStaticSamePadding(
        32, 16, kernel_size=(1, 1), stride=(1, 1), bias=False
        (static_padding): Identity()
      )
      (_bn2): GroupNorm(4, 16, ep

In [11]:
teacher_model_weights = {}
for name, param in teacher_model.named_parameters():
    teacher_model_weights[name] = param.detach()

In [12]:
def rand_bbox(size, lam):
    W = size[2]
    H = size[3]
    cut_rat = np.sqrt(1. - lam)
    cut_w = np.int(W * cut_rat)
    cut_h = np.int(H * cut_rat)

    # uniform
    cx = np.random.randint(W)
    cy = np.random.randint(H)

    bbx1 = np.clip(cx - cut_w // 2, 0, W)
    bby1 = np.clip(cy - cut_h // 2, 0, H)
    bbx2 = np.clip(cx + cut_w // 2, 0, W)
    bby2 = np.clip(cy + cut_h // 2, 0, H)

    return bbx1, bby1, bbx2, bby2

In [13]:
def reg_cls(model):
    l2_cls = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if name.startswith(fc_name):
            l2_cls += 0.5 * torch.norm(param) ** 2
    return l2_cls

def reg_l2sp(model):
    sp_loss = torch.tensor(0.).cuda()
    for name, param in model.named_parameters():
        if not name.startswith(fc_name):
            sp_loss += 0.5 * torch.norm(param - teacher_model_weights[name]) ** 2
    return sp_loss

# Loss

In [14]:
criterion = nn.CrossEntropyLoss().cuda()
optimizer = optim.SGD(student_model.parameters(), lr=lr, momentum=momentum)
# optimizer = optim.Adam(model.parameters(), weight_decay=0)
scheduler_cosine = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, epochs)
scheduler_warmup = GradualWarmupScheduler(optimizer, multiplier=4, total_epoch=50, after_scheduler=scheduler_cosine)

In [15]:
# Resume
if resume:
    print('==> Resuming from checkpoint..')
    checkpoint = os.path.dirname(resume)
#     checkpoint = torch.load(resume)
    resume = torch.load(resume)
    best_acc = resume['best_acc']
    start_epoch = resume['epoch']
    student_model.load_state_dict(resume['state_dict'])
    optimizer.load_state_dict(resume['optimizer'])
    logger = Logger(os.path.join(checkpoint, 'log.txt'), resume=True)
else:
    logger = Logger(os.path.join(checkpoint, 'log.txt'))
    logger.set_names(['Learning Rate', 'Train Loss', 'Valid Loss', 'Train Acc.', 'Valid Acc.', 'Source Loss', 'Source ACC.'])

# Train

In [16]:
def train(train_loader, source_train_loader, teacher_model, student_model, criterion, optimizer, epoch, use_cuda):
    student_model.train()
    torch.set_grad_enabled(True)
    
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()
    end = time.time()
    
    source_set = []
    for inputs, targets in source_train_loader:
        source_set.append((inputs, targets))
    
    bar = Bar('Processing', max=len(train_loader))
    for batch_idx, (inputs, targets) in enumerate(train_loader):
        batch_size = inputs.size(0)
        if batch_size < train_batch:
            continue
        # measure data loading time
        data_time.update(time.time() - end)

        if use_cuda:
            inputs, targets = inputs.cuda(), targets.cuda()
        inputs, targets = torch.autograd.Variable(inputs), torch.autograd.Variable(targets)
        
        # cutmix
        source_inputs, source_targets = source_set[batch_idx]
        source_inputs, source_targets = source_inputs.cuda(), source_targets.cuda()

        prob_delta = cm_prob_init - cm_prob_low
        prob_step = epoch / (epochs+1) * prob_delta
        lam = cm_prob_init - prob_step

        rand_index = torch.randperm(inputs.size()[0]).cuda()
        st = source_targets[rand_index]
        tt = targets[rand_index]
        rand_index = rand_index[st == tt]

        bbx1, bby1, bbx2, bby2 = rand_bbox(inputs.size(), 1-lam)
        inputs[rand_index, :, bbx1:bbx2, bby1:bby2] = source_inputs[rand_index, :, bbx1:bbx2, bby1:bby2]
        lam = 1 - ((bbx2 - bbx1)*(bby2 - bby1) / (inputs.size()[-1] * inputs.size()[-2]))
        
        outputs = student_model(inputs)
        loss_main = criterion(outputs, targets)
        loss_cls = 0
        loss_sp = 0
        loss_cls = reg_cls(student_model)
        loss_sp = reg_l2sp(student_model)
            
            
        # compute output
        loss = loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

        # measure accuracy and record loss
        prec1 = accuracy(outputs.data, targets.data)
        losses.update(loss.data.tolist(), inputs.size(0))
        top1.update(prec1[0], inputs.size(0))

        # compute gradient and do SGD step
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        # plot progress
        bar.suffix  = '({batch}/{size}) Data: {data:.3f}s | Batch: {bt:.3f}s | Total: {total:} | ETA: {eta:} | Loss: {loss:.4f} | top1: {top1: .4f} '.format(
                    batch=batch_idx + 1,
                    size=len(train_loader),
                    data=data_time.val,
                    bt=batch_time.val,
                    total=bar.elapsed_td,
                    eta=bar.eta_td,
                    loss=losses.avg,
                    top1=top1.avg,
                    )
        bar.next()
#         if batch_idx % 10 == 0:
        print('{batch}/{size} Data:{data:.3f} | Batch:{bt:.3f} | Total:{total:} | ETA:{eta:} | Loss:{loss:} | top1:{tp1:}'.format(
                 batch=batch_idx+1, size=len(train_loader), data=data_time.val, bt=batch_time.val, total=bar.elapsed_td, eta=bar.eta_td, loss=losses.avg, tp1=top1.avg))
    bar.finish()
    return (losses.avg, top1.avg)

In [17]:
def test(val_loader, model, criterion, epoch, use_cuda):
    global best_acc

    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    top1 = AverageMeter()

    # switch to evaluate mode
    model.eval()
    torch.set_grad_enabled(False)

    end = time.time()
    bar = Bar('Processing', max=len(val_loader))
    for batch_idx, (inputs, targets) in enumerate(val_loader):
        # measure data loading time
        data_time.update(time.time() - end)

        if use_cuda:
            inputs, targets = inputs.cuda(), targets.cuda()
        inputs, targets = torch.autograd.Variable(inputs, volatile=True), torch.autograd.Variable(targets)

        # compute output
        outputs = model(inputs)
        loss_main = criterion(outputs, targets)
        loss_cls = 0
        loss_sp = 0
        loss_cls = reg_cls(model)
        loss_sp = reg_l2sp(model)
        loss = loss_main + sp_alpha*loss_sp + sp_beta*loss_cls

        # measure accuracy and record loss
        prec1 = accuracy(outputs.data, targets.data)
        losses.update(loss.data.tolist(), inputs.size(0))
        top1.update(prec1[0], inputs.size(0))

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        # plot progress
        bar.suffix  = '({batch}/{size}) Data: {data:.3f}s | Batch: {bt:.3f}s | Total: {total:} | ETA: {eta:} | Loss: {loss:} | top1: {top1:}'.format(
                    batch=batch_idx + 1,
                    size=len(val_loader),
                    data=data_time.avg,
                    bt=batch_time.avg,
                    total=bar.elapsed_td,
                    eta=bar.eta_td,
                    loss=losses.avg,
                    top1=top1.avg,)
        bar.next()
    print('{batch}/{size} Data:{data:.3f} | Batch:{bt:.3f} | Total:{total:} | ETA:{eta:} | Loss:{loss:} | top1:{tp1:}'.format(
         batch=batch_idx+1, size=len(val_loader), data=data_time.val, bt=batch_time.val, total=bar.elapsed_td, eta=bar.eta_td, loss=losses.avg, tp1=top1.avg))
    bar.finish()
    return (losses.avg, top1.avg)

In [18]:
def save_checkpoint(state, is_best, checkpoint='checkpoint', filename='checkpoint.pth.tar'):
    filepath = os.path.join(checkpoint, filename)
    torch.save(state, filepath)
    if is_best:
        shutil.copyfile(filepath, os.path.join(checkpoint, 'model_best.pth.tar'))

def adjust_learning_rate(optimizer, epoch):
    global state
    lr_set = [1, 1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
    lr_list = schedule.copy()
    lr_list.append(epoch)
    lr_list.sort()
    idx = lr_list.index(epoch)
    state['lr'] *= lr_set[idx]
    for param_group in optimizer.param_groups:
        param_group['lr'] = state['lr']

In [ ]:
for epoch in range(start_epoch, epochs):
    # teacher feedback
    if epoch in iter_time:
        print("iterative training: feedback {}".format(epoch))
        teacher_model.load_state_dict(student_model.state_dict())
        teacher_model_weights = {}
        for name, param in teacher_model.named_parameters():
            teacher_model_weights[name] = param.detach()
    
    state['lr'] = optimizer.state_dict()['param_groups'][0]['lr']
    adjust_learning_rate(optimizer, epoch)
    print('\nEpoch: [%d | %d] LR: %f' % (epoch + 1, epochs, state['lr']))
    
    train_loss, train_acc = train(source_train_loader, train_loader, teacher_model, student_model, criterion, optimizer, epoch, use_cuda)
    
    if epoch % 20 == 0:
        test_loss, test_acc = test(val_target_loader, student_model, criterion, epoch, use_cuda)
        source_loss, source_acc = test(val_source_loader, student_model, criterion, epoch, use_cuda)

    
        logger.append([state['lr'], train_loss, test_loss, train_acc, test_acc, source_loss, source_acc])
        is_best = test_acc > best_acc
        best_acc = max(test_acc, best_acc)
        save_checkpoint({
            'epoch': epoch + 1,
            'state_dict' : student_model.state_dict(),
            'acc': test_acc,
            'best_acc': best_acc,
            'optimizer': optimizer.state_dict(),
        }, is_best, checkpoint=checkpoint)
    scheduler_warmup.step()


Epoch: [1 | 5000] LR: 0.030000
1/17 Data:7.894 | Batch:22.970 | Total:0:00:17 | ETA:0:04:33 | Loss:1.673294186592102 | top1:66.66667175292969
2/17 Data:0.003 | Batch:3.883 | Total:0:00:20 | ETA:0:02:37 | Loss:1.9608978629112244 | top1:62.5
3/17 Data:0.001 | Batch:3.731 | Total:0:00:24 | ETA:0:01:56 | Loss:1.5470431844393413 | top1:69.44444274902344
4/17 Data:0.001 | Batch:3.298 | Total:0:00:27 | ETA:0:01:31 | Loss:1.616940751671791 | top1:70.83333587646484
5/17 Data:0.001 | Batch:3.572 | Total:0:00:31 | ETA:0:01:16 | Loss:1.6301597237586976 | top1:75.00000762939453
6/17 Data:0.001 | Batch:3.476 | Total:0:00:34 | ETA:0:01:05 | Loss:1.6266113817691803 | top1:77.77777862548828
7/17 Data:0.001 | Batch:4.118 | Total:0:00:39 | ETA:0:00:56 | Loss:1.7266162378447396 | top1:76.19047546386719
8/17 Data:0.001 | Batch:2.861 | Total:0:00:41 | ETA:0:00:48 | Loss:1.7264077737927437 | top1:77.08333587646484
9/17 Data:0.001 | Batch:4.046 | Total:0:00:46 | ETA:0:00:41 | Loss:1.7437718643082514 | top1:7

/home/cutz/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:21: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.


39/39 Data:0.004 | Batch:0.426 | Total:0:00:52 | ETA:0:00:00 | Loss:2.074342348636725 | top1:52.37179183959961
161/161 Data:0.005 | Batch:2.093 | Total:0:02:32 | ETA:0:00:00 | Loss:1.4464107785269478 | top1:98.40499114990234

Epoch: [2 | 5000] LR: 0.031800
1/17 Data:0.985 | Batch:1.290 | Total:0:00:00 | ETA:0:00:11 | Loss:1.6797192096710205 | top1:83.33332824707031
2/17 Data:0.018 | Batch:0.294 | Total:0:00:00 | ETA:0:00:07 | Loss:1.7146210074424744 | top1:79.16667175292969
3/17 Data:0.005 | Batch:0.280 | Total:0:00:01 | ETA:0:00:06 | Loss:1.6332664092381795 | top1:86.11111450195312
4/17 Data:0.019 | Batch:0.281 | Total:0:00:01 | ETA:0:00:05 | Loss:1.6227291226387024 | top1:85.41667175292969
5/17 Data:0.023 | Batch:0.300 | Total:0:00:01 | ETA:0:00:05 | Loss:1.6643835067749024 | top1:83.33333587646484
6/17 Data:0.009 | Batch:0.279 | Total:0:00:02 | ETA:0:00:04 | Loss:1.6667709549268086 | top1:83.33333587646484
7/17 Data:0.021 | Batch:0.280 | Total:0:00:02 | ETA:0:00:04 | Loss:1.69111345

8/17 Data:0.005 | Batch:0.272 | Total:0:00:03 | ETA:0:00:04 | Loss:1.1998308598995209 | top1:86.45833587646484
9/17 Data:0.002 | Batch:0.275 | Total:0:00:03 | ETA:0:00:04 | Loss:1.2088509930504694 | top1:87.03704071044922
10/17 Data:0.032 | Batch:0.336 | Total:0:00:03 | ETA:0:00:03 | Loss:1.213686966896057 | top1:87.50000762939453
11/17 Data:0.025 | Batch:0.327 | Total:0:00:04 | ETA:0:00:03 | Loss:1.2425798069347034 | top1:86.36363983154297
12/17 Data:0.032 | Batch:0.325 | Total:0:00:04 | ETA:0:00:02 | Loss:1.3040283719698589 | top1:81.94444274902344
13/17 Data:0.025 | Batch:0.319 | Total:0:00:04 | ETA:0:00:02 | Loss:1.2943039949123676 | top1:82.05128479003906
14/17 Data:0.013 | Batch:0.270 | Total:0:00:05 | ETA:0:00:01 | Loss:1.301386637347085 | top1:80.95238494873047
15/17 Data:0.006 | Batch:0.268 | Total:0:00:05 | ETA:0:00:01 | Loss:1.319335110982259 | top1:79.44444274902344
16/17 Data:0.014 | Batch:0.280 | Total:0:00:05 | ETA:0:00:01 | Loss:1.3195939511060715 | top1:78.645835876464

1/17 Data:7.545 | Batch:7.831 | Total:0:00:00 | ETA:0:00:09 | Loss:0.6609976887702942 | top1:100.0
2/17 Data:0.005 | Batch:0.284 | Total:0:00:00 | ETA:0:00:07 | Loss:0.6467869281768799 | top1:100.0
3/17 Data:0.021 | Batch:0.311 | Total:0:00:01 | ETA:0:00:06 | Loss:0.6838846206665039 | top1:97.22222137451172
4/17 Data:0.027 | Batch:0.306 | Total:0:00:01 | ETA:0:00:05 | Loss:0.6876483857631683 | top1:97.91667175292969
5/17 Data:0.011 | Batch:0.299 | Total:0:00:01 | ETA:0:00:05 | Loss:0.8009225845336914 | top1:95.00000762939453
6/17 Data:0.016 | Batch:0.299 | Total:0:00:02 | ETA:0:00:04 | Loss:0.8234869142373403 | top1:93.05555725097656
7/17 Data:0.031 | Batch:4.719 | Total:0:00:06 | ETA:0:00:10 | Loss:0.7999572839055743 | top1:92.85714721679688
8/17 Data:0.001 | Batch:4.396 | Total:0:00:11 | ETA:0:00:13 | Loss:0.7856632247567177 | top1:93.75
9/17 Data:0.001 | Batch:0.783 | Total:0:00:11 | ETA:0:00:11 | Loss:0.8258170220586989 | top1:91.66666412353516
10/17 Data:0.002 | Batch:0.330 | Tota

...

6/17 Data:0.000 | Batch:0.303 | Total:0:00:02 | ETA:0:00:05 | Loss:0.00043115078976067406 | top1:100.0
7/17 Data:0.000 | Batch:0.261 | Total:0:00:02 | ETA:0:00:05 | Loss:0.00043479519497070996 | top1:100.0
8/17 Data:0.001 | Batch:0.272 | Total:0:00:03 | ETA:0:00:04 | Loss:0.0006424020975828171 | top1:100.0
9/17 Data:0.001 | Batch:0.276 | Total:0:00:03 | ETA:0:00:04 | Loss:0.0024374303304486806 | top1:100.0
10/17 Data:0.008 | Batch:0.358 | Total:0:00:03 | ETA:0:00:03 | Loss:0.0022592787398025395 | top1:100.00000762939453
11/17 Data:0.004 | Batch:0.508 | Total:0:00:04 | ETA:0:00:03 | Loss:0.0020937189189928836 | top1:100.0
12/17 Data:0.003 | Batch:0.285 | Total:0:00:04 | ETA:0:00:02 | Loss:0.0019442404955043457 | top1:100.0
13/17 Data:0.001 | Batch:0.471 | Total:0:00:05 | ETA:0:00:02 | Loss:0.0018275461132781436 | top1:100.0
14/17 Data:0.001 | Batch:0.311 | Total:0:00:05 | ETA:0:00:02 | Loss:0.0036833547762528595 | top1:100.0
15/17 Data:0.002 | Batch:0.511 | Total:0:00:05 | ETA:0:00:01 |

2/17 Data:0.002 | Batch:0.785 | Total:0:00:02 | ETA:0:00:19 | Loss:0.006137055068393238 | top1:100.0
3/17 Data:0.001 | Batch:0.459 | Total:0:00:02 | ETA:0:00:14 | Loss:0.004283696442143992 | top1:100.0
4/17 Data:0.001 | Batch:0.622 | Total:0:00:03 | ETA:0:00:12 | Loss:0.00332841574709164 | top1:100.0
5/17 Data:0.001 | Batch:0.671 | Total:0:00:04 | ETA:0:00:11 | Loss:0.003457109868759289 | top1:100.00000762939453
6/17 Data:0.001 | Batch:0.560 | Total:0:00:04 | ETA:0:00:09 | Loss:0.003060989241930656 | top1:100.0
7/17 Data:0.001 | Batch:0.546 | Total:0:00:05 | ETA:0:00:08 | Loss:0.0030142084537406583 | top1:100.0
8/17 Data:0.000 | Batch:0.269 | Total:0:00:05 | ETA:0:00:07 | Loss:0.0026851674883801024 | top1:100.0
9/17 Data:0.001 | Batch:0.315 | Total:0:00:05 | ETA:0:00:06 | Loss:0.0024579629179142 | top1:100.0
10/17 Data:0.001 | Batch:0.346 | Total:0:00:06 | ETA:0:00:05 | Loss:0.002350544012733735 | top1:100.00000762939453
11/17 Data:0.001 | Batch:0.511 | Total:0:00:06 | ETA:0:00:04 | Lo

15/17 Data:0.001 | Batch:0.620 | Total:0:00:09 | ETA:0:00:02 | Loss:0.0020850397743439925 | top1:100.0
16/17 Data:0.001 | Batch:0.623 | Total:0:00:10 | ETA:0:00:01 | Loss:0.0020038849161210237 | top1:100.0

Epoch: [2837 | 5000] LR: 0.000493
1/17 Data:2.292 | Batch:2.783 | Total:0:00:01 | ETA:0:00:18 | Loss:0.00037105692899785936 | top1:100.0
2/17 Data:0.001 | Batch:0.342 | Total:0:00:01 | ETA:0:00:11 | Loss:0.0007625997968716547 | top1:100.0
3/17 Data:0.001 | Batch:0.434 | Total:0:00:01 | ETA:0:00:09 | Loss:0.0006258372547260175 | top1:100.0
4/17 Data:0.001 | Batch:0.374 | Total:0:00:02 | ETA:0:00:08 | Loss:0.0005696352091035806 | top1:100.0
5/17 Data:0.001 | Batch:0.430 | Total:0:00:02 | ETA:0:00:07 | Loss:0.08036493148538285 | top1:98.33333587646484
6/17 Data:0.001 | Batch:0.290 | Total:0:00:02 | ETA:0:00:06 | Loss:0.06703375238187921 | top1:98.61111450195312
7/17 Data:0.002 | Batch:0.356 | Total:0:00:03 | ETA:0:00:05 | Loss:0.05752207994061921 | top1:98.80952453613281
8/17 Data:0.00

10/17 Data:0.002 | Batch:0.569 | Total:0:00:04 | ETA:0:00:04 | Loss:0.017440348892705515 | top1:98.33333587646484
11/17 Data:0.001 | Batch:0.511 | Total:0:00:05 | ETA:0:00:03 | Loss:0.015948997752275318 | top1:98.48484802246094
12/17 Data:0.001 | Batch:0.442 | Total:0:00:05 | ETA:0:00:03 | Loss:0.01465118814909753 | top1:98.61111450195312
13/17 Data:0.003 | Batch:0.519 | Total:0:00:06 | ETA:0:00:02 | Loss:0.013679670839337632 | top1:98.71794891357422
14/17 Data:0.001 | Batch:0.655 | Total:0:00:07 | ETA:0:00:02 | Loss:0.012730686278830814 | top1:98.80952453613281
15/17 Data:0.001 | Batch:0.479 | Total:0:00:07 | ETA:0:00:01 | Loss:0.011908156151184813 | top1:98.8888931274414
16/17 Data:0.003 | Batch:0.401 | Total:0:00:07 | ETA:0:00:01 | Loss:0.011204053707842831 | top1:98.95833587646484
39/39 Data:1.043 | Batch:1.218 | Total:0:00:21 | ETA:0:00:00 | Loss:2.216698637375465 | top1:54.166664123535156
161/161 Data:0.000 | Batch:0.152 | Total:0:00:36 | ETA:0:00:00 | Loss:0.06895979932245343 | 

5/17 Data:0.001 | Batch:0.363 | Total:0:00:02 | ETA:0:00:07 | Loss:0.0005989085417240858 | top1:100.00000762939453
6/17 Data:0.001 | Batch:0.424 | Total:0:00:02 | ETA:0:00:06 | Loss:0.000554686591688854 | top1:100.0
7/17 Data:0.000 | Batch:0.392 | Total:0:00:03 | ETA:0:00:05 | Loss:0.0005551099353137293 | top1:100.0
8/17 Data:0.001 | Batch:0.298 | Total:0:00:03 | ETA:0:00:05 | Loss:0.000545955521374708 | top1:100.0
9/17 Data:0.000 | Batch:0.261 | Total:0:00:03 | ETA:0:00:04 | Loss:0.0005590722721535712 | top1:100.0
10/17 Data:0.000 | Batch:0.282 | Total:0:00:04 | ETA:0:00:03 | Loss:0.0006438080599764362 | top1:100.00000762939453
11/17 Data:0.000 | Batch:0.408 | Total:0:00:04 | ETA:0:00:03 | Loss:0.0006191974574573 | top1:100.0
12/17 Data:0.001 | Batch:0.407 | Total:0:00:04 | ETA:0:00:03 | Loss:0.0005983872106298804 | top1:100.0
13/17 Data:0.000 | Batch:0.446 | Total:0:00:05 | ETA:0:00:02 | Loss:0.0005860466447372276 | top1:100.0
14/17 Data:0.001 | Batch:0.362 | Total:0:00:05 | ETA:0:00